In [1]:
! pip install --quiet transformers shap sentencepiece datasets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.9/547.9 kB 25.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.6/519.6 kB 38.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.8/294.8 kB 31.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 45.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 49.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 20.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.9 MB/s eta 0:00:00


In [2]:
import transformers
import shap
import torch
import datasets

import numpy as np
import scipy as sp

from transformers import AutoTokenizer, AutoModelForCausalLM, AutoModelForSeq2SeqLM, DistilBertTokenizerFast, DistilBertForSequenceClassification

# Text Generation

## gpt2

In [3]:
tokenizer = AutoTokenizer.from_pretrained("gpt2", use_fast=True)
model = AutoModelForCausalLM.from_pretrained("gpt2").cuda()

In [4]:
# set model decoder to true
model.config.is_decoder=True
# set text-generation params under task_specific_params
model.config.task_specific_params["text-generation"] = {
    "do_sample": True,
    "max_length": 50,
    "temperature": 0.7,
    "top_k": 50,
    "no_repeat_ngram_size": 2,
    "max_new_tokens": 25
}

In [4]:
s = ['Text generation works by utilizing algorithms and language models to process input data and']

In [13]:
explainer = shap.Explainer(model, tokenizer)
shap_values = explainer(s)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


  0%|          | 0/182 [00:00<?, ?it/s]

Partition explainer: 2it [00:14, 14.04s/it]               


In [14]:
shap.plots.text(shap_values)

## gpt2-medium

In [3]:
tokenizer2 = AutoTokenizer.from_pretrained("gpt2-medium", use_fast=True)
model2 = AutoModelForCausalLM.from_pretrained("gpt2-medium").cuda()

In [7]:
# set model decoder to true
model2.config.is_decoder=True
# set text-generation params under task_specific_params
model2.config.task_specific_params["text-generation"] = {
    "do_sample": True,
    "max_length": 50,
    "temperature": 0.7,
    "top_k": 50,
    "no_repeat_ngram_size": 2,
    "max_new_tokens": 25
}

In [8]:
explainer = shap.Explainer(model2, tokenizer2)
shap_values = explainer(s)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


  0%|          | 0/182 [00:00<?, ?it/s]

Partition explainer: 2it [00:12, 12.83s/it]               


In [9]:
shap.plots.text(shap_values)

## google/flan-t5-base

In [12]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

In [13]:
tokenizer3 = T5Tokenizer.from_pretrained("google/flan-t5-base")
model3 = T5ForConditionalGeneration.from_pretrained("google/flan-t5-base").cuda()

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. If you see this, DO NOT PANIC! This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thouroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


In [14]:
explainer = shap.Explainer(model3, tokenizer3)
shap_values = explainer(s)

Using the model-agnostic default `max_length` (=20) to control thegeneration length. We recommend setting `max_new_tokens` to control the maximum length of the generation.


  0%|          | 0/240 [00:00<?, ?it/s]

In [15]:
shap.plots.text(shap_values)